In [1]:
# Dependencies
# ----------------------------------
import pandas as pd

# Imports the method used for connecting to DBs
from sqlalchemy import create_engine

# Imports the methods needed to abstract classes into tables
from sqlalchemy.ext.declarative import declarative_base

# Allow us to declare column types
from sqlalchemy import Column, Integer, String, Float 

from sqlalchemy import create_engine, Column, Integer, String, ForeignKey
Base = declarative_base()

In [2]:
oscars_df = pd.read_csv('output/final_oscars.csv')
imdb_df = pd.read_csv('output/cleaned_imdb.csv')

In [3]:
# Create the Classes
class Directors(Base):
    __tablename__ = 'directors'
    director_id = Column(String, primary_key=True)
    director_name = Column(String(255))
    
class Movies(Base):
    __tablename__ = 'movies'
    movie_id = Column(String, primary_key=True)
    movie_title = Column(String(255))
    year = Column(Integer)
    director_id = Column(String(255), ForeignKey('directors.director_id'))
    reviews_from_users = Column(Float)
    reviews_from_critics = Column(Float)

class Oscar_categories(Base):
    __tablename__ = 'oscar_categories'
    oscar_id = Column(String, primary_key=True)
    award_category = Column(String(255))
    
class Movie_awards(Base):
    __tablename__ = 'movie_awards'
    movie_id = Column(String, ForeignKey('movies.movie_id'), primary_key=True)
    oscar_id = Column(String(255), ForeignKey('oscar_categories.oscar_id'), primary_key=True)

class Directing_awards(Base):
    __tablename__ = 'directing_awards'
    director_id = Column(String, ForeignKey('directors.director_id'), primary_key=True)
    oscar_id = Column(String(255), ForeignKey('oscar_categories.oscar_id'), primary_key=True)

In [4]:
# These tables only exists in python and not in the actual database
Base.metadata.tables

immutabledict({'directors': Table('directors', MetaData(bind=None), Column('director_id', String(), table=<directors>, primary_key=True, nullable=False), Column('director_name', String(length=255), table=<directors>), schema=None), 'movies': Table('movies', MetaData(bind=None), Column('movie_id', String(), table=<movies>, primary_key=True, nullable=False), Column('movie_title', String(length=255), table=<movies>), Column('year', Integer(), table=<movies>), Column('director_id', String(length=255), ForeignKey('directors.director_id'), table=<movies>), Column('reviews_from_users', Float(), table=<movies>), Column('reviews_from_critics', Float(), table=<movies>), schema=None), 'oscar_categories': Table('oscar_categories', MetaData(bind=None), Column('oscar_id', String(), table=<oscar_categories>, primary_key=True, nullable=False), Column('award_category', String(length=255), table=<oscar_categories>), schema=None), 'movie_awards': Table('movie_awards', MetaData(bind=None), Column('movie_i

In [5]:
database = "movies_db"
username = 'postgres'
password = '868789'
host = 'localhost'
port = 5432

In [6]:
# Create our database engine
engine = create_engine(f"postgresql://{username}:{password}@{host}:{port}/{database}") 

In [7]:
# This is where we create our tables in the database
Base.metadata.create_all(engine)

In [8]:
# The ORM’s “handle” to the database is the Session.
from sqlalchemy.orm import Session
session = Session(engine)

In [9]:
# Read csv for directors
directors_df = pd.read_csv('output/directors.csv',  index_col=0)
directors_df

name
0                            Alexander Black
1                               Charles Tait
2                                  Urban Gad
3                         Charles L. Gaskill
4                        Francesco Bertolini
...                                      ...
36590                         Geethika Sudip
36591                             Steve Noir
36592                           Erik Verkerk
36593   Syed Nurfaiz Khalid bin Syed Ibrahim
36594                         Nando Martínez

[36595 rows x 1 columns]

In [10]:
# Note that adding to the session does not update the table. It queues up those queries.
# Adding data to directors table from directors csv file
count = 0
for name in directors_df['name']:
    session.add(Directors(director_id=count, director_name=name))
    count +=1

In [11]:
session.new

IdentitySet([<__main__.Directors object at 0x0000019BB7739940>, <__main__.Directors object at 0x0000019BB77399B0>, <__main__.Directors object at 0x0000019BB7739828>, <__main__.Directors object at 0x0000019BB7739898>, <__main__.Directors object at 0x0000019BB7739A90>, <__main__.Directors object at 0x0000019BB7739B00>, <__main__.Directors object at 0x0000019BB7739B70>, <__main__.Directors object at 0x0000019BB7739BE0>, <__main__.Directors object at 0x0000019BB7739C50>, <__main__.Directors object at 0x0000019BB7739CC0>, <__main__.Directors object at 0x0000019BB7739D30>, <__main__.Directors object at 0x0000019BB7739DA0>, <__main__.Directors object at 0x0000019BB7739E10>, <__main__.Directors object at 0x0000019BB7739E80>, <__main__.Directors object at 0x0000019BB7739EF0>, <__main__.Directors object at 0x0000019BB7739F60>, <__main__.Directors object at 0x0000019BB7739FD0>, <__main__.Directors object at 0x0000019BB774E080>, <__main__.Directors object at 0x0000019BB774E0F0>, <__main__.Director

In [12]:
session.commit()

In [13]:
imdb_df = pd.read_csv('output/cleaned_imdb.csv',  index_col=0)
imdb_df

imdb_title_id                           title  year  \
0         tt0000009                      Miss Jerry  1894   
1         tt0000574     The Story of the Kelly Gang  1906   
2         tt0001892                  Den sorte drøm  1911   
3         tt0002101                       Cleopatra  1912   
4         tt0002130                       L'Inferno  1911   
...             ...                             ...   ...   
85850     tt9908390                         Le lion  2020   
85851     tt9911196  De Beentjes van Sint-Hildegard  2020   
85852     tt9911774       Padmavyuhathile Abhimanyu  2019   
85853     tt9914286               Sokagin Çocuklari  2019   
85854     tt9914942      La vida sense la Sara Amat  2019   

                           genre           country  \
0                        Romance               USA   
1        Biography, Crime, Drama         Australia   
2                          Drama  Germany, Denmark   
3                 Drama, History               USA   
4      Adventure, Drama, Fantasy             Italy   
...                          ...               ...   
85850                     Comedy   France, Belgium   
85851              Comedy, Drama       Netherlands   
85852                      Drama             India   
85853              Drama, Family            Turkey   
85854                      Drama             Spain   

                                  director  \
0                          Alexander Black   
1                             Charles Tait   
2                                Urban Gad   
3                       Charles L. Gaskill   
4      Francesco Bertolini, Adolfo Padovan   
...                                    ...   
85850               Ludovic Colbeau-Justin   
85851                      Johan Nijenhuis   
85852                      Vineesh Aaradya   
85853                    Ahmet Faik Akinci   
85854                            Laura Jou   

                                      writer             production_company  \
0                            Alexander Black     Alexander Black Photoplays   
1                               Charles Tait                 J. and N. Tait   
2      Urban Gad, Gebhard Schätzler-Perasini                       Fotorama   
3                           Victorien Sardou  Helen Gardner Picture Players   
4                            Dante Alighieri                    Milano Film   
...                                      ...                            ...   
85850  Alexandre Coquelle, Matthieu Le Naour              Monkey Pack Films   
85851           Radek Bajgar, Herman Finkers           Johan Nijenhuis & Co   
85852       Vineesh Aaradya, Vineesh Aaradya               RMCC Productions   
85853         Ahmet Faik Akinci, Kasim Uçkan                    Gizem Ajans   
85854                   Coral Cruz, Pep Puig  La Xarxa de Comunicació Local   

       reviews_from_users  reviews_from_critics  
0                     1.0                   2.0  
1                     7.0                   7.0  
2                     5.0                   2.0  
3                    25.0                   3.0  
4                    31.0                  14.0  
...                   ...                   ...  
85850                 NaN                   4.0  
85851                 6.0                   4.0  
85852                 NaN                   NaN  
85853                 NaN                   NaN  
85854                 NaN                   2.0  

[85855 rows x 10 columns]

In [14]:
# Adding data to movies table from imdb csv file
for index, name in imdb_df.iterrows():
    session.add(Movies(movie_id=name['imdb_title_id'], movie_title=name['title'], year=name['year'], reviews_from_users=name['reviews_from_users'], reviews_from_critics=name['reviews_from_critics']))


In [15]:
session.new

IdentitySet([<__main__.Movies object at 0x0000019BB6CCC518>, <__main__.Movies object at 0x0000019BB6CCCE48>, <__main__.Movies object at 0x0000019BB6CCCA58>, <__main__.Movies object at 0x0000019BB6CCC5C0>, <__main__.Movies object at 0x0000019BB6CCC390>, <__main__.Movies object at 0x0000019BB6CCC7B8>, <__main__.Movies object at 0x0000019BB6CCC198>, <__main__.Movies object at 0x0000019BB6CCC940>, <__main__.Movies object at 0x0000019BB6CCC898>, <__main__.Movies object at 0x0000019BB6CCCA90>, <__main__.Movies object at 0x0000019BB6CCCC18>, <__main__.Movies object at 0x0000019BB6CCCE10>, <__main__.Movies object at 0x0000019BB047D588>, <__main__.Movies object at 0x0000019BB244A278>, <__main__.Movies object at 0x0000019BB44545C0>, <__main__.Movies object at 0x0000019BB64E9F98>, <__main__.Movies object at 0x0000019BB6CA7EF0>, <__main__.Movies object at 0x0000019BBC185898>, <__main__.Movies object at 0x0000019BBC185E48>, <__main__.Movies object at 0x0000019BBC1857F0>, <__main__.Movies object at 

In [16]:
session.commit()

In [17]:
# Read csv for oscars categories
oscars_categories = pd.read_csv('output/oscars_categories.csv',  index_col=0)
oscars_categories

categories
0                         DIRECTING
1  CINEMATOGRAPHY (Black-and-White)
2            CINEMATOGRAPHY (Color)
3               BEST MOTION PICTURE
4                      BEST PICTURE

In [18]:
# Adding data to oscars categories table from csv file
count = 0
for index, name in oscars_categories.iterrows():
    session.add(Oscar_categories(oscar_id=count, award_category=name['categories']))
    count +=1

In [19]:
session.commit()

In [25]:
movie_awards = pd.read_csv('output/movie_awards.csv',  index_col=0)
movie_awards.head()

title_id  oscar_id
139    tt0163246         0
171    tt3598108         0
234    tt0427047         0
360    tt0020025         0
1503  tt10497826         0

In [27]:
# Adding data to movie_awards relationship table from csv file
for index, name in movie_awards.iterrows():
    session.add(Movie_awards(movie_id=name['title_id'], oscar_id=name['oscar_id']))

In [28]:
session.commit()

In [21]:
# Directing_awards
# director_id
# oscar_id

In [ ]:
session.close()